In [1]:
!pip install --user nglview  #Устанавливаем пакет для визуализации структур биомакромолекул

/usr/lib/python3/dist-packages/secretstorage/dhcrypto.py:15: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/usr/lib/python3/dist-packages/secretstorage/util.py:19: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
You should consider upgrading via the '/usr/bin/python3 -m pip install --upgrade pip' command.


In [2]:
import nglview as nv #Импортируем необходимое
import requests
import json

In [3]:
my_query = {"query": {"type": "group",       #Начинаем формировать запрос
                      "logical_operator": "and",
                      "nodes": []},
            "return_type": "entry"}

In [4]:
keyword_clause = {"type": "terminal",     #Будем добавлять условия запроса. Первое из них - ключевое слово "ibuprofen"
                  "service": "full_text",
                  "parameters": {"value": "ibuprofen"}}
my_query["query"]["nodes"].append(keyword_clause)

In [5]:
date_range_clause = {"type": "terminal",   #Требуемая дата публикации записи: с января 2010 года по январь 2015 года
                     "service": "text",
                     "parameters": {"attribute": "rcsb_accession_info.initial_release_date",
                                    "operator": "range",
                                    "value": {"from": "2010-01-01",
                                              "to": "2015-01-01"}}}
my_query["query"]["nodes"].append(date_range_clause)

In [6]:
resolution_clause = {"type": "terminal", #Добавим в запрос условие про разрешение: оно должно быть не хуже 2.6 ангстрем
                     "service": "text",
                     "parameters": {"attribute": "rcsb_entry_info.resolution_combined",
                                    "operator": "less_or_equal",
                                    "value": 2.6}}
my_query["query"]["nodes"].append(resolution_clause)

In [7]:
ligand_clause = {"type": "terminal", #И последнее условие: лигандов должно быть не меньше 2
                 "service": "text",
                 "parameters": {"attribute": "rcsb_entry_info.nonpolymer_entity_count",
                                "operator": "greater",
                                "value": 1}}
my_query["query"]["nodes"].append(ligand_clause)

In [8]:
rcsb = 'https://search.rcsb.org/rcsbsearch/v1/query' #Отправляем запрос на сервер RSCB
json_query = json.dumps(my_query)
search = requests.post(f'{rcsb}', data=json_query)

In [9]:
search_result=search.json() #Сохраняем полученный ответ в нужном формате

In [10]:
best_hit = search_result["result_set"][0] #Выбираем лучшую находку

In [11]:
best_hit #Лучшая находка

{'identifier': '3VM4',
 'score': 0.981454454397083,
 'services': [{'service_type': 'text',
   'nodes': [{'node_id': 4766, 'original_score': 1.0, 'norm_score': 1.0},
    {'node_id': 12450, 'original_score': 1.0, 'norm_score': 1.0},
    {'node_id': 21967, 'original_score': 1.0, 'norm_score': 1.0}]},
  {'service_type': 'full_text',
   'nodes': [{'node_id': 11540,
     'original_score': 13.912753105163574,
     'norm_score': 0.9258178175883319}]}]}

In [12]:
Итак, далее я буду работать с PDB ID 3VM4. Приступим к визуализации.

In [ ]:
from ipywidgets import interact, fixed #Импортируем необходимое

In [ ]:
representations=[  #Отображение можно сделать, пользуясь различными типами, которые приведены ниже
  'ball+stick',      # шаростержневая модель
  'backbone',        # прямые линии, соединяющие С-альфа атомы
  'cartoon',         # условное отображение вторичной структуры
  'helixorient',     # упрощенное отображение 
  'hyperball',       # сглаженная шаростержневая модель
  'licorice',        # стержневая модель (без шаров)
  'line',            # очень тонкая стержневая модель
  'point',           # атомы в виде плоских точек
  'ribbon',          # отображение остова в виде ленты
  'rocket',          # отображение альфа-спиралей как цилиндров
  'rope',            # отображение остова в виде колбасы
  'spacefill',       # атомы в виде шаров соотв. Ван-дер-Ваальсова радиуса
  'surface',         # поверхность
  'trace',           # сглаженная линия, соединяющая С-альфа атомы
  'tube'             # более сдержанный rope
]

In [ ]:
colors=[     #Также есть различные варианты покраски молекул
  'random',
  'uniform',
  'atomindex',      # от синего к красному с ростом номера атома
  'residueindex',   # от синего к красному с ростом номера остатка
  'chainindex',     # каждой цепи свой цвет
  'sstruc',         # стандартные цвета для типа вторичной структуры
  'element',        # стандартные цвета для химических элементов
  'resname',        # свой цвет каждому из 20 остатков
  'bfactor',        # чем темнее, тем подвижнее
  'hydrophobicity', # чем темнее, тем гидрофобнее
]

In [ ]:
my_displays={  #Создадим словарь, в котором опишем желаемые варианты отображений
'Отображение 1': {'description':
'''Белок из записи 3VM4 в виде tube с покраской 
по типу вторичной структуры.
Боковые радикалы в стержневой модели, покрашены по гидрофобности.
Лиганды показаны линиями, покрашены по элементам.
Вода и ионы показаны в виде Ван-дер-Ваальсовых сфер.''',
                               'representations': [{'type': 'tube',
                                                    'params': {'sele': 'protein',
                                                               'color': 'sstruc'}},
                                                   {'type': 'licorice',
                                                    'params': {'sele': 'sidechainAttached',
                                                               'color': 'hydrophobicity'}},
                                                   {'type': 'line',
                                                    'params': {'sele': 'ligand',
                                                               'color': 'element'}},
                                                   {'type': 'spacefill',
                                                    'params': {'sele': 'water and ion'}}]},
'Отображение 2': {'description': 
'''Белок из записи 3VM4 в виде cartoon темно-серого цвета.
Боковые радикалы в виде линий светло-серого цвета.
Боковые радикалы полярных аминокислот в виде hyperball, покрашены по элементам.
Лиганды в шаростержневой модели, покрашены по элементам, углероды покрашены в темно-синий.''',
                               'representations': [{'type': 'cartoon',
                                                    'params': {'sele': 'protein',
                                                               'color': 'darkgrey'}},
                                                   {'type': 'line',
                                                    'params': {'sele': 'sidechainAttached',
                                                               'color': 'lightgrey'}},
                                                   {'type': 'hyperball',
                                                    'params': {'sele': 'sidechainAttached and polar',
                                                               'color': 'element'}},
                                                    {'type': 'ball+stick',
                                                    'params': {'sele': 'ligand and not _C',
                                                               'color': 'element'}},
                                                   {'type': 'ball+stick',
                                                    'params': {'sele': 'ligand and _C',
                                                               'color': 'darkblue'}}]},
'Отображение 3': {'description':
'''Поверхность белка из записи 3VM4 покрашена в белый, с непрозрачностью 0.1.
Белок в виде cartoon темно-серого цвета.
Боковые радикалы в стержневой модели, покрашены по гидрофобности.
Лиганды в виде Ван-дер-Ваальсовых сфер, покрашены по элементам.''',
                               'representations': [{'type': 'surface',
                                                    'params': {'sele': 'protein',
                                                               'color': 'white',
                                                               'opacity': 0.1}},
                                                   {'type': 'cartoon',
                                                    'params': {'sele': 'protein',
                                                               'color': 'darkgrey'}},
                                                   {'type': 'licorice',
                                                    'params': {'sele': 'sidechainAttached',
                                                               'color': 'hydrophobicity'}},
                                                   {'type': 'spacefill',
                                                    'params': {'sele': 'ligand',
                                                               'color': 'element'}}]}}

In [ ]:
def show_displays(view, image_name): #Визуализируем
    view.clear()
    img=my_displays[image_name]
    print(img['description'])
    view.set_representations(img['representations'])
    view.center()
view = nv.show_pdbid("3vm4", default_representation=False)
interact(show_displays, view=fixed(view), image_name=list(my_displays.keys()))
view